## 1. Подготовка данных

In [8]:
import pandas as pd
import os
from multiprocessing import Pool
import shutil
from sklearn.model_selection import train_test_split

df = pd.read_csv(r'..\moderatsiya-kartochek-5706-master\data\private_info\train.csv', sep='	')

current_dir = os.path.join(r'..\model\..')

dirs_main = [(i for i in os.listdir(os.path.join(current_dir, r'moderatsiya-kartochek-5706-master\data\train', i))) for i in os.listdir(os.path.join(current_dir, r'moderatsiya-kartochek-5706-master\data\train'))]
dirs = os.listdir(os.path.join(current_dir, r'moderatsiya-kartochek-5706-master\data\train'))
dict_images = {i: [] for i in dirs}

if not os.path.exists(os.path.join(r'data\smoking')):
    os.makedirs(os.path.join(r'data\smoking'))
if not os.path.exists(os.path.join(r'data\not_smoking')):
    os.makedirs(os.path.join(r'data\not_smoking'))

for dir in range(len(dirs_main)):
    for file in dirs_main[dir]:
        with Pool(8) as p:
            try:
                class_for_file = df.loc[df['image_name']==file]['label_id'].to_list()[0]
            except:
                continue
            if class_for_file == 0:
                shutil.copy(os.path.join(current_dir, r'moderatsiya-kartochek-5706-master\data\train', dirs[dir], file), os.path.join(r'data\not_smoking', file))
            else:
                shutil.copy(os.path.join(current_dir, r'moderatsiya-kartochek-5706-master\data\train', dirs[dir], file), os.path.join(r'data\smoking', file))

if not os.path.exists(os.path.join('dataset')):
    os.makedirs(os.path.join('dataset'))

dirs = [[r'train\smoking', r'val\smoking', r'test\smoking'], [r'train\not_smoking', r'val\not_smoking', r'test\not_smoking']]
for l in dirs:
    for dir in l:
        if not os.path.exists(os.path.join(r'dataset', dir)):
            os.makedirs(os.path.join(r'dataset', dir))

dir_datas = [i for i in os.listdir(os.path.join(r'data')) if i.endswith(r'smoking')]
files = [os.listdir(os.path.join(os.path.join(r'data', i))) for i in dir_datas]

train_smoking, val_smoking = train_test_split(files[1], test_size=0.3, random_state=42)
val_smoking, test_smoking = train_test_split(val_smoking, test_size=0.5, random_state=42)
train_not_smoking, val_not_smoking = train_test_split(files[0], test_size=0.3, random_state=42)
val_not_smoking, test_not_smoking = train_test_split(val_not_smoking, test_size=0.5, random_state=42)

train_files = [[train_smoking, val_smoking, test_smoking], [train_not_smoking, val_not_smoking, test_not_smoking]]

for i in range(len(train_files)):
    for j in range(len(train_files[i])):
        for file in train_files[i][j]:
            if i == 0:
                shutil.copy(os.path.join(r'data\smoking', file), os.path.join(r'dataset', dirs[i][j], file))
            else:
                shutil.copy(os.path.join(r'data\not_smoking', file), os.path.join(r'dataset', dirs[i][j], file))



In [ ]:
import albumentations as A
import cv2
 
transform = A.Compose(
    [
        A.RandomRotate90(),
        A.Flip(),
        A.Transpose(p=0.8),
        A.GaussNoise(p=0.6),
        A.OneOf([
            A.MotionBlur(p=.2),
            A.MedianBlur(blur_limit=3, p=0.1),
            A.Blur(blur_limit=3, p=0.1),
        ], p=0.2),
        A.ShiftScaleRotate(shift_limit=0.0625, scale_limit=0.2, rotate_limit=45, p=0.2),
        A.OneOf([
            A.OpticalDistortion(p=0.4),
            A.GridDistortion(p=.3),
        ], p=0.2),
        A.OneOf([
            A.CLAHE(clip_limit=2),
            A.RandomBrightnessContrast(p=0.4),
        ], p=0.3),
        A.HueSaturationValue(p=0.3),
        A.ShiftScaleRotate(p=0.5)
    ]
)

def transofrm_image(image, transform, num):
            transformed = transform(image=image)
            transformed_image = transformed['image']

            file_transformed = file[:file.find('.')]+str(f'_{num}.jpg')

            return {
                 'name':file_transformed,
                 'image': transformed_image
                }

def save_image(image, file, dir):
      cv2.imwrite(os.path.join(dir, file), image)

for file in train_smoking:
    image = cv2.imread(os.path.join(r'dataset\train\smoking', file))
    with Pool(8) as p:
        try:
            images = (transofrm_image(image, transform, num=i) for i in range(1, 6))
        except:
            continue
    for j in images:
        with Pool(8) as p:    
            save_image(file=j['name'], image=j['image'], dir=r'dataset\train\smoking')



print('_________________________________________________________')

for file in train_not_smoking:
    image = cv2.imread(os.path.join(r'dataset\train\not_smoking', file))
    with Pool(8) as p:
        try:
            images = (transofrm_image(image, transform, num=i) for i in range(1, 6))
        except:
            continue
    for j in images:
        with Pool(8) as p:    
            save_image(file=j['name'], image=j['image'], dir=r'dataset\train\not_smoking')

test_dict = {'image': [], 'label': []}
for i in range(len(train_files)):
    test_dict['image'] += train_files[i][-1]
    if i == 0:
        test_dict['label'] += [1] * len(train_files[i][-1])
    else:
        test_dict['label'] += [0] * len(train_files[i][-1])

df = pd.DataFrame(test_dict)
df.to_csv('test_score_annotations.csv', index=False)

annotations_dict = {'image': [], 'label': []}
for i in range(len(dirs)):
    for dir in dirs[i]:
        for file in os.listdir(os.path.join(r'dataset', dir)):
            if i == 0:
                annotations_dict['image'].append(file)
                annotations_dict['label'].append(1) 
            else:
                annotations_dict['image'].append(file)
                annotations_dict['label'].append(0) 

df = pd.DataFrame(annotations_dict)
df.to_csv('annotations_for_scores.csv', index=False)


___________________

## 2. Обучение модели

# Tune3 - SGD new
# Tune4 - AdamW new
# HyperParamsTuneSGD2 - new params
# AdamW - without params
# HyperParamsTuneAdamW2 - new params

In [14]:
from ultralytics import YOLO

model = YOLO('yolov8x-cls.pt')

#### 2.1 SGD optimizer

* 2.1.1 Тюнинг параметров

In [2]:
model_tune_SGD = model.tune(data=r'dataset', iterations=1000, epochs=200, optimizer='SGD', plots=True, save=True, val=True, device='GPU', name='Tuning')

Tuner: Initialized Tuner instance with 'tune_dir=runs\classify\tune3'
Tuner:  Learn about tuning at https://docs.ultralytics.com/guides/hyperparameter-tuning
Tuner: Starting iteration 1/1000 with hyperparameters: {'lr0': 0.01, 'lrf': 0.01, 'momentum': 0.937, 'weight_decay': 0.0005, 'warmup_epochs': 3.0, 'warmup_momentum': 0.8, 'box': 7.5, 'cls': 0.5, 'dfl': 1.5, 'hsv_h': 0.015, 'hsv_s': 0.7, 'hsv_v': 0.4, 'degrees': 0.0, 'translate': 0.1, 'scale': 0.5, 'shear': 0.0, 'perspective': 0.0, 'flipud': 0.0, 'fliplr': 0.5, 'bgr': 0.0, 'mosaic': 1.0, 'mixup': 0.0, 'copy_paste': 0.0}
WARNING  training failure for hyperparameter tuning iteration 1
Command '['yolo', 'train', 'task=classify', 'mode=train', 'model=yolov8x-cls.pt', 'data=dataset', 'epochs=200', 'time=None', 'patience=100', 'batch=16', 'imgsz=224', 'save=True', 'save_period=-1', 'cache=False', 'device=GPU', 'workers=8', 'project=None', 'name=Tuning', 'exist_ok=False', 'pretrained=True', 'optimizer=SGD', 'verbose=True', 'seed=0', 'dete

* 2.1.2 Обучение сети

In [3]:
model_train_SGD = model.train(data=r'dataset', epochs=150, optimizer='SGD', plots=True, save=True, val=True, device='GPU', name='HyperParamsTuneSGD', lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, 
                          warmup_epochs=3.0, warmup_momentum=0.8, box=7.5, cls=0.5, dfl=1.5, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, 
                          fliplr=0.5, bgr=.0, mosaic=1.0, mixup=0.0, copy_paste=0.0)

New https://pypi.org/project/ultralytics/8.2.81 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.80  Python-3.9.19 torch-2.4.0 CUDA:gpu (NVIDIA GeForce RTX 4080 SUPER, 16376MiB)
engine\trainer: task=classify, mode=train, model=yolov8x-cls.pt, data=dataset, epochs=150, time=None, patience=100, batch=16, imgsz=224, save=True, save_period=-1, cache=False, device=GPU, workers=8, project=None, name=HyperParamsTuneSGD2, exist_ok=False, pretrained=True, optimizer=SGD, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, show=

c:\Users\artem\anaconda3\envs\yolo\lib\site-packages\ultralytics\engine\trainer.py:271: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(enabled=self.amp)
train: Scanning C:\Users\artem\OneDrive\Рабочий стол\HackOzon\model\dataset\train... 22158 images, 0 corrupt: 100%|██████████| 22158/22158 [00:04<00:00, 4585.05it/s]

train: WARNING  C:\Users\artem\OneDrive\ \HackOzon\model\dataset\train\not_smoking\notsmoking_0742.jpg: corrupt JPEG restored and saved


train: New cache created: C:\Users\artem\OneDrive\ \HackOzon\model\dataset\train.cache


val: Scanning C:\Users\artem\OneDrive\Рабочий стол\HackOzon\model\dataset\val... 791 images, 0 corrupt: 100%|██████████| 791/791 [00:00<00:00, 3681.94it/s]

...

    102/150      2.19G    0.03481         14        224: 100%|██████████| 1385/1385 [00:56<00:00, 24.66it/s]
               classes   top1_acc   top5_acc: 100%|██████████| 25/25 [00:01<00:00, 17.53it/s]

                   all      0.949          1
EarlyStopping: Training stopped early as no improvement observed in last 100 epochs. Best results observed at epoch 2, best model saved as best.pt.
To update EarlyStopping(patience=100) pass a new patience value, i.e. `patience=300` or use `patience=0` to disable EarlyStopping.



102 epochs completed in 1.677 hours.
Optimizer stripped from runs\classify\HyperParamsTuneSGD2\weights\last.pt, 112.5MB
Optimizer stripped from runs\classify\HyperParamsTuneSGD2\weights\best.pt, 112.5MB

Validating runs\classify\HyperParamsTuneSGD2\weights\best.pt...
Ultralytics YOLOv8.2.80  Python-3.9.19 torch-2.4.0 CUDA:0 (NVIDIA GeForce RTX 4080 SUPER, 16376MiB)
YOLOv8x-cls summary (fused): 133 layers, 56,125,762 parameters, 0 gradients
train: C:\Users\artem\OneDrive\ \HackOzon\model\dataset\train... found 22158 images in 2 classes  
val: C:\Users\artem\OneDrive\ \HackOzon\model\dataset\val... found 791 images in 2 classes  
test: C:\Users\artem\OneDrive\ \HackOzon\model\dataset\test... found 793 images in 2 classes  


               classes   top1_acc   top5_acc: 100%|██████████| 25/25 [00:01<00:00, 19.07it/s]


                   all      0.961          1
Speed: 0.1ms preprocess, 0.4ms inference, 0.0ms loss, 0.0ms postprocess per image
Results saved to runs\classify\HyperParamsTuneSGD2
Results saved to runs\classify\HyperParamsTuneSGD2


* 2.1.3 Получение метрик: Precision, Recall, f1score

In [6]:
import pandas as pd
from sklearn.metrics import f1_score, recall_score, precision_score

model_SGD = YOLO(r'runs\classify\HyperParamsTuneSGD2\weights\best.pt')

y_true = pd.read_csv(r'test_score_annotations.csv')['label']

In [9]:
predictions_SGD = [model.predict(os.path.join('dataset', 'test', 'smoking', i))[0].probs.top1 for i in test_smoking]

predictions_SGD += [model.predict(os.path.join('dataset', 'test', 'not_smoking', i))[0].probs.top1 for i in test_not_smoking]


image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\smoking_000066.jpg: 224x224 smoking 1.00, not_smoking 0.00, 4.0ms
Speed: 70.4ms preprocess, 4.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\sigars_000107.jpg: 224x224 smoking 0.99, not_smoking 0.01, 4.0ms
Speed: 7.5ms preprocess, 4.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\pipe_000533.jpg: 224x224 smoking 0.91, not_smoking 0.09, 6.5ms
Speed: 4.0ms preprocess, 6.5ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\smoking_001373.jpg: 224x224 smoking 1.00, not_smoking 0.00, 4.0ms
Speed: 4.0ms preprocess, 4.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\tes

* * 2.1.3.1 Precision

In [10]:
precision_score(y_true, predictions_SGD)

0.9633699633699634

* * 2.1.3.2 Recall

In [11]:
recall_score(y_true, predictions_SGD)

0.9131944444444444

* * 2.1.3.3 F1 score

In [12]:
f1_score(y_true, predictions_SGD)

0.9376114081996435

#### 2.1 AdamW optimizer

* 2.1.1 Тюнинг параметров

In [13]:
model_tune_AdamW = model.tune(data=r'dataset', iterations=1000, epochs=200, optimizer='AdamW', plots=True, save=True, val=True, device='GPU', name='Tuning')

Tuner: Initialized Tuner instance with 'tune_dir=runs\classify\tune4'
Tuner:  Learn about tuning at https://docs.ultralytics.com/guides/hyperparameter-tuning
Tuner: Starting iteration 1/1000 with hyperparameters: {'lr0': 0.01, 'lrf': 0.01, 'momentum': 0.937, 'weight_decay': 0.0005, 'warmup_epochs': 3.0, 'warmup_momentum': 0.8, 'box': 7.5, 'cls': 0.5, 'dfl': 1.5, 'hsv_h': 0.015, 'hsv_s': 0.7, 'hsv_v': 0.4, 'degrees': 0.0, 'translate': 0.1, 'scale': 0.5, 'shear': 0.0, 'perspective': 0.0, 'flipud': 0.0, 'fliplr': 0.5, 'bgr': 0.0, 'mosaic': 1.0, 'mixup': 0.0, 'copy_paste': 0.0}
WARNING  training failure for hyperparameter tuning iteration 1
Command '['yolo', 'train', 'task=classify', 'mode=train', 'model=yolov8x-cls.pt', 'data=dataset', 'epochs=200', 'time=None', 'patience=100', 'batch=16', 'imgsz=224', 'save=True', 'save_period=-1', 'cache=False', 'device=GPU', 'workers=8', 'project=None', 'name=Tuning', 'exist_ok=False', 'pretrained=True', 'optimizer=AdamW', 'verbose=True', 'seed=0', 'de

* 2.1.2 Обучение сети

In [17]:
model_train_AdamW = model.train(data=r'dataset', epochs=150, optimizer='AdamW', plots=True, save=True, val=True, device='GPU', name='HyperParamsTuneAdamW', lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, 
                          warmup_epochs=3.0, warmup_momentum=0.8, box=7.5, cls=0.5, dfl=1.5, hsv_h=0.015, hsv_s=0.7, hsv_v=0.4, degrees=0.0, translate=0.1, scale=0.5, shear=0.0, perspective=0.0, flipud=0.0, 
                          fliplr=0.5, bgr=0.0, mosaic=1.0, mixup=0.0, copy_paste=0.0)

New https://pypi.org/project/ultralytics/8.2.81 available  Update with 'pip install -U ultralytics'
Ultralytics YOLOv8.2.80  Python-3.9.19 torch-2.4.0 CUDA:gpu (NVIDIA GeForce RTX 4080 SUPER, 16376MiB)
engine\trainer: task=classify, mode=train, model=yolov8x-cls.pt, data=dataset, epochs=150, time=None, patience=100, batch=16, imgsz=224, save=True, save_period=-1, cache=False, device=GPU, workers=8, project=None, name=HyperParamsTuneAdamW2, exist_ok=False, pretrained=True, optimizer=AdamW, verbose=True, seed=0, deterministic=True, single_cls=False, rect=False, cos_lr=False, close_mosaic=10, resume=False, amp=True, fraction=1.0, profile=False, freeze=None, multi_scale=False, overlap_mask=True, mask_ratio=4, dropout=0.0, val=True, split=val, save_json=False, save_hybrid=False, conf=None, iou=0.7, max_det=300, half=False, dnn=False, plots=True, source=None, vid_stride=1, stream_buffer=False, visualize=False, augment=False, agnostic_nms=False, classes=None, retina_masks=False, embed=None, s

c:\Users\artem\anaconda3\envs\yolo\lib\site-packages\ultralytics\engine\trainer.py:271: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(enabled=self.amp)
train: Scanning C:\Users\artem\OneDrive\Рабочий стол\HackOzon\model\dataset\train... 22158 images, 0 corrupt: 100%|██████████| 22158/22158 [00:00<?, ?it/s]

train: WARNING  C:\Users\artem\OneDrive\ \HackOzon\model\dataset\train\not_smoking\notsmoking_0742.jpg: corrupt JPEG restored and saved



val: Scanning C:\Users\artem\OneDrive\Рабочий стол\HackOzon\model\dataset\val... 791 images, 0 corrupt: 100%|██████████| 791/791 [00:00<?, ?it/s]


optimizer: AdamW(lr=0.01, momentum=0.937) with parameter groups 50 weight(decay=0.0), 51 weight(decay=0.0005), 51 bias(decay=0.0)
Image sizes 224 train, 224 val
Using 8 dataloader workers
Logging results to runs\classify\HyperParamsTuneAdamW2
Starting training for 150 epochs...

      Epoch    GPU_mem       loss  Instances       Size


...

     10/150       2.9G     0.4338         14        224: 100%|██████████| 1385/1385 [01:01<00:00, 22.52it/s]
               classes   top1_acc   top5_acc: 100%|██████████| 25/25 [00:01<00:00, 22.45it/s]

                   all      0.637          1



      Epoch    GPU_mem       loss  Instances       Size


     11/150      2.89G     0.4359         14        224: 100%|██████████| 1385/1385 [01:01<00:00, 22.57it/s]
               classes   top1_acc   top5_acc: 100%|██████████| 25/25 [00:01<00:00, 17.79it/s]

                   all      0.637          1


* 2.1.3 Получение метрик: Precision, Recall, f1score

In [19]:
model_AdamW = YOLO(r'runs\classify\HyperParamsTuneSGD\weights\best.pt')

In [20]:
predictions_AdamW = [model.predict(os.path.join('dataset', 'test', 'smoking', i))[0].probs.top1 for i in test_smoking]

predictions_AdamW += [model.predict(os.path.join('dataset', 'test', 'not_smoking', i))[0].probs.top1 for i in test_not_smoking]


image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\smoking_000156_3.jpg: 224x224 smoking 0.73, not_smoking 0.27, 7.0ms
Speed: 11.2ms preprocess, 7.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\smoking_val_000522_2.jpg: 224x224 smoking 0.55, not_smoking 0.45, 7.0ms
Speed: 4.0ms preprocess, 7.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\smoking_000631_1.jpg: 224x224 smoking 0.58, not_smoking 0.42, 7.0ms
Speed: 3.0ms preprocess, 7.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOzon\model\dataset\test\smoking\smoking_val_001299_5.jpg: 224x224 smoking 0.65, not_smoking 0.35, 9.0ms
Speed: 2.0ms preprocess, 9.0ms inference, 0.0ms postprocess per image at shape (1, 3, 224, 224)

image 1/1 c:\Users\artem\OneDrive\ \HackOz

* * 2.1.3.1 Precision

In [21]:
precision_score(y_true, predictions_AdamW)

0.8092307692307692

* * 2.1.3.2 Recall

In [22]:
recall_score(y_true, predictions_AdamW)


0.7325905292479109

* * 2.1.3.3 F1 score

In [23]:
f1_score(y_true, predictions_AdamW)

0.7690058479532164

: 

_______________